In [ ]:
# from google.colab import drive
# drive.mount('/content/drive')

In [ ]:
! pip install --upgrade numpy pandas tqdm torch catalyst==20.09

In [1]:
import os
import json
import pickle
from bisect import bisect_left, bisect_right
from datetime import datetime, timedelta
from collections import defaultdict, Counter

import numpy as np
import pandas as pd
from tqdm import tqdm

# GPU hack if you need
os.environ["CUDA_VISIBLE_DEVICES"] = "0"

# Data

Columns
- `party_rk` – client unique identifier
- `account_rk` – client account unique identifier
- `financial_account_type_cd` – debit/credit card flag
- `transaction_dttm` – operation datetime
- `transaction_type_desc` – purchase/payment/...
- `transaction_amt_rur` – transaction price
- `merchant_type` - DUTY FREE STORES/FUEL DEALERS/RESTAURANTS/ etc
- `merchant_group_rk` - McDonald's/Wildberries/ etc

It's important that table is already sorted by `transaction_dttm` column!!!

In [2]:
DATADIR = "./hackathon_data" # "./data"
transactions_path = f"{DATADIR}/avk_hackathon_data_transactions.csv"
pd.read_csv(f"{DATADIR}/avk_hackathon_data_transactions.csv", nrows=5)

party_rk  account_rk  financial_account_type_cd transaction_dttm  \
0     20337       19666                          1       2019-01-01   
1     63404       72991                          1       2019-01-01   
2     24789       23517                          2       2019-01-01   
3     57970       64838                          2       2019-01-01   
4     12232       11591                          2       2019-01-01   

  transaction_type_desc  transaction_amt_rur  merchant_rk  merchant_type  \
0               Покупка                84.00      88676.0          348.0   
1               Покупка               410.00     887248.0          330.0   
2               Покупка               701.44     830014.0          291.0   
3               Покупка              6203.70     363834.0          278.0   
4               Покупка               734.53      85919.0          286.0   

   merchant_group_rk      category  
0                NaN      Сувениры  
1              725.0      Фаст Фуд  
2                NaN  Супермаркеты  
3              454.0    Дом/Ремонт  
4              878.0  Супермаркеты

## Mappings
~1 min

In [ ]:
# Prepare & save mappings
mappings = defaultdict(dict)
unk_token = "<UNK>"


def create_mapping(values):
    mapping = {unk_token: 0}
    for v in values:
        if not pd.isna(v):
            mapping[str(v)] = len(mapping)

    return mapping


for col in tqdm(
    [
        "transaction_type_desc",
        "merchant_rk",
        "merchant_type",
        "merchant_group_rk",
        "category",
        "financial_account_type_cd",
    ]
):

    col_values = (
        pd.read_csv(transactions_path, usecols=[col])[col]
        .fillna(unk_token)
        .astype(str)
    )
    mappings[col] = create_mapping(col_values.unique())
    del col_values


with open(f"{DATADIR}/mappings.json", "w") as f:
    json.dump(mappings, f)

In [3]:
# load mappings
with open(f"{DATADIR}/mappings.json", 'r') as f:
    mappings = json.load(f)

## Parse transactions by users
~ 40 min

In [ ]:
# Prepare & save client data
party2dates = defaultdict(list)  # for each party save a series of the transaction dates 
party2sum = defaultdict(list)  # for each party save a series of the transaction costs 
party2merchant_type = defaultdict(list)  # for each party save a series of the transaction_type 
party2trans_type = defaultdict(list)  # for each party save a series of the transaction merchant_type

usecols = [
    "party_rk",
    "transaction_dttm",
    "transaction_amt_rur",
    "merchant_type",
    "transaction_type_desc",
]

for chunk in tqdm(
    pd.read_csv(transactions_path, usecols=usecols, chunksize=100_000)
):

    chunk["merchant_type"] = (
        chunk["merchant_type"].fillna(unk_token).astype(str)
    )
    chunk["transaction_type_desc"] = (
        chunk["transaction_type_desc"].fillna(unk_token).astype(str)
    )
    chunk["transaction_amt_rur"] = chunk["transaction_amt_rur"].fillna(0)

    for i, row in chunk.iterrows():
        party2dates[row.party_rk].append(row.transaction_dttm)
        party2sum[row.party_rk].append(row.transaction_amt_rur)
        party2merchant_type[row.party_rk].append(
            mappings["merchant_type"][row.merchant_type]
        )
        party2trans_type[row.party_rk].append(
            mappings["transaction_type_desc"][row.transaction_type_desc]
        )

    del chunk

pickle.dump(party2dates, open(f"{DATADIR}/party2dates.pkl", "wb"))
pickle.dump(party2sum, open(f"{DATADIR}/party2sum.pkl", "wb"))
pickle.dump(party2merchant_type, open(f"{DATADIR}/party2merchant_type.pkl", "wb"))
pickle.dump(party2trans_type, open(f"{DATADIR}/party2trans_type.pkl", "wb"))

In [4]:
# load client data
party2dates = pickle.load(open(f"{DATADIR}/party2dates.pkl", 'rb'))
party2sum = pickle.load(open(f"{DATADIR}/party2sum.pkl", 'rb'))
party2merchant_type = pickle.load(open(f"{DATADIR}/party2merchant_type.pkl", 'rb'))
party2trans_type = pickle.load(open(f"{DATADIR}/party2trans_type.pkl", 'rb'))

## PyTorch dataset

In [5]:
from sklearn.model_selection import train_test_split

train_party, valid_party = train_test_split(
    pd.read_csv(transactions_path, usecols=['party_rk']).party_rk.unique(), 
    train_size=0.8, random_state=42
)

print(f'Train: {len(train_party)} Val: {len(valid_party)}')

Train: 40000 Val: 10000


In [6]:
predict_period_len = 60  # -- days
train_predict_dates = (
    pd.date_range("2019-03-01", "2019-10-31", freq="MS")
    .strftime("%Y-%m-%d")
    .tolist()
)
valid_predict_dates = (
    pd.date_range("2019-11-01", "2019-12-31", freq="MS")
    .strftime("%Y-%m-%d")
    .tolist()
)
submission_predict_dates = (
    pd.date_range("2020-01-01", "2020-02-28", freq="2MS")
    .strftime("%Y-%m-%d")
    .tolist()
)

In [7]:
def prepare_data(party_list, mode="train"):
    """
    This function define the pipeline of the creation of train and valid samples.
    We consider each client from party_list. For each client take each 
    predict_period_start from predict_dates list. All client transaction before
    this date is our features. Next, we look at the customer's transactions in 
    the next two months. This transactions should be predicted. It will form 
    our labels vector.
    """

    data_sum = []
    data_trans_type = []
    data_merchant_type = []
    data_labels = []

    for party_rk in tqdm(party_list):
        date_series = party2dates[party_rk]
        sum_series = party2sum[party_rk]
        merch_type_series = party2merchant_type[party_rk]
        trans_type_series = party2trans_type[party_rk]

        if mode == "train":
            predict_dates = train_predict_dates
        elif mode == "valid":
            predict_dates = valid_predict_dates
        elif mode == "submission":
            predict_dates = submission_predict_dates
        else:
            raise Exception("Unknown mode")

        for predict_period_start in predict_dates:

            predict_period_end = datetime.strftime(
                datetime.strptime(predict_period_start, "%Y-%m-%d")
                + timedelta(days=predict_period_len),
                "%Y-%m-%d",
            )

            l, r = (
                bisect_left(date_series, predict_period_start),
                bisect_right(date_series, predict_period_end),
            )

            history_merch_type = merch_type_series[:l]
            history_sum = sum_series[:l]
            history_trans_type = trans_type_series[:l]
            predict_merch = merch_type_series[l:r]

            if predict_merch and l or mode not in ("train", "valid"):
                data_sum.append(history_sum)
                data_trans_type.append(history_trans_type)
                data_merchant_type.append(history_merch_type)
                data_labels.append(predict_merch)

    return data_sum, data_trans_type, data_merchant_type, data_labels

In [8]:
train_sum, train_trans_type, train_merchant_type, train_labels = prepare_data(
    train_party, mode="train"
)
valid_sum, valid_trans_type, valid_merchant_type, valid_labels = prepare_data(
    valid_party, mode="valid"
)

100%|██████████| 10000/10000 [00:01<00:00, 5164.16it/s]


## PyTorch loaders

In [24]:
import torch
from torch.utils.data import Dataset, DataLoader

In [25]:
MERCH_TYPE_NCLASSES = len(mappings['merchant_type'])
TRANS_TYPE_NCLASSES = len(mappings['transaction_type_desc'])
PADDING_LEN = 300

In [26]:
class RSDataset(Dataset):
    def __init__(self, data_sum, data_trans_type, data_merchant_type, labels):
        super(RSDataset, self).__init__()
        self.data_sum = data_sum
        self.data_trans_type = data_trans_type
        self.data_merchant_type = data_merchant_type
        self.labels = labels

    def __len__(self):
        return len(self.data_sum)

    def __getitem__(self, idx):
        targets = np.zeros((MERCH_TYPE_NCLASSES - 1,), dtype=np.float32)
        for m in self.labels[idx]:
            if m:  # skip UNK, UNK-token should not be predicted
                targets[m - 1] = 1.0

        item = {
            "features": {},
            "targets": targets,
        }

        sum_feature = np.array(self.data_sum[idx][-PADDING_LEN:])
        sum_feature = np.vectorize(lambda s: np.log(1 + s))(sum_feature)
        if sum_feature.shape[0] < PADDING_LEN:
            pad = np.zeros(
                (PADDING_LEN - sum_feature.shape[0],), dtype=np.float32
            )
            sum_feature = np.hstack((sum_feature, pad))
        item["features"]["sum"] = torch.from_numpy(sum_feature).float()

        for feature_name, feature_values in zip(
            ["trans_type", "merchant_type"],
            [self.data_trans_type[idx], self.data_merchant_type[idx]],
        ):

            feature_values = np.array(feature_values[-PADDING_LEN:])
            mask = np.ones(feature_values.shape[0], dtype=np.float32)
            if feature_values.shape[0] < PADDING_LEN:
                feature_values = np.append(
                    feature_values,
                    np.zeros(
                        PADDING_LEN - feature_values.shape[0], dtype=np.int64
                    ),
                )
                mask = np.append(
                    mask,
                    np.zeros(PADDING_LEN - mask.shape[0], dtype=np.float32),
                )
            item["features"][feature_name] = torch.from_numpy(feature_values).long()
            item["features"][f"{feature_name}_mask"] = torch.from_numpy(mask).float()

        return item

In [27]:
train_dataset = RSDataset(
    train_sum, train_trans_type, train_merchant_type, train_labels
)
valid_dataset = RSDataset(
    valid_sum, valid_trans_type, valid_merchant_type, valid_labels
)


In [28]:
train_loader = DataLoader(
    train_dataset, batch_size=64, shuffle=True, num_workers=4
)
valid_loader = DataLoader(
    valid_dataset, batch_size=64, shuffle=False, num_workers=4
)

In [29]:
# sanity check
# for i in tqdm(range(len(train_loader))):
#     batch = next(iter(train_loader))

## Model

This is the baseline model for predicting purchases in `merchant_type` in the next 2 months

In [30]:
import torch.nn as nn
from collections import OrderedDict

In [31]:
params = {
    'merchant_type_emb_dim': 64,
    'trans_type_embedding': 3,
    'transformer_nhead': 2,
    'transformer_dim_feedforward': 256,
    'transformer_dropout': 0.1,
    'dense_unit': 256,
    'num_layers': 4,
}

In [32]:
MERCH_TYPE_NCLASSES, TRANS_TYPE_NCLASSES

(458, 5)

In [33]:
class Model(nn.Module):
    def __init__(self):
        super().__init__()

        self.merchant_type_embedding = nn.Embedding(
            MERCH_TYPE_NCLASSES, params["merchant_type_emb_dim"]
        )
        self.trans_type_embedding = nn.Embedding(
            TRANS_TYPE_NCLASSES, params["trans_type_embedding"]
        )

        embedding_size = (
            params["merchant_type_emb_dim"]
            + params["trans_type_embedding"]
            + 1
        )

        transformer_blocks = []
        for i in range(params["num_layers"]):
            transformer_block = nn.TransformerEncoderLayer(
                d_model=embedding_size,
                nhead=params["transformer_nhead"],
                dim_feedforward=params["transformer_dim_feedforward"],
                dropout=params["transformer_dropout"],
            )
            transformer_blocks.append(
                (f"transformer_block_{i}", transformer_block)
            )

        self.transformer_encoder = nn.Sequential(
            OrderedDict(transformer_blocks)
        )

        self.linear = nn.Linear(
            in_features=embedding_size, out_features=params["dense_unit"]
        )
        self.scorer = nn.Linear(
            in_features=params["dense_unit"],
            out_features=MERCH_TYPE_NCLASSES - 1,
        )

    def forward(self, features):

        merchant_type_emb = self.merchant_type_embedding(features["merchant_type"])
        trans_type_emb = self.trans_type_embedding(features["trans_type"])

        merchant_type_emb = merchant_type_emb * features["merchant_type_mask"].unsqueeze(-1)
        trans_type_emb = trans_type_emb * features["trans_type_mask"].unsqueeze(-1)

        embeddings = torch.cat(
            (merchant_type_emb, trans_type_emb, features["sum"].unsqueeze(-1)),
            dim=-1,
        )

        transformer_output = self.transformer_encoder(embeddings)
        pooling = torch.mean(transformer_output, dim=1)
        linear = torch.tanh(self.linear(pooling))
        merch_logits = self.scorer(linear)

        return merch_logits

### One-batch-check

In [34]:
%%time 

model = Model()
criterion = nn.BCEWithLogitsLoss()
batch = next(iter(train_loader))
output = model(batch['features'])
loss = criterion(output, batch['targets'])
print(loss)

tensor(0.7028, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
CPU times: user 1.37 s, sys: 876 ms, total: 2.25 s
Wall time: 504 ms


## Train loop with [Catalyst](https://github.com/catalyst-team/catalyst)

[A comprehensive step-by-step guide to basic and advanced features](https://github.com/catalyst-team/catalyst#step-by-step-guide).

---



In [35]:
from catalyst import dl, utils
from catalyst.utils import metrics

## Custom metrics for this hackathon

In [36]:
from typing import List, Optional, Sequence, Tuple, Union

import numpy as np
import torch
from catalyst.utils.metrics.functional import preprocess_multi_label_metrics
from catalyst.utils.torch import get_activation_fn


def multi_label_metrics(
    outputs: torch.Tensor,
    targets: torch.Tensor,
    threshold: Union[float, torch.Tensor],
    activation: Optional[str] = None,
    eps: float = 1e-7,
) -> Tuple[torch.Tensor, torch.Tensor, torch.Tensor, torch.Tensor]:
    """
    Computes multi-label precision for the specified activation and threshold.

    Args:
        outputs (torch.Tensor): NxK tensor that for each of the N examples
            indicates the probability of the example belonging to each of
            the K classes, according to the model.
        targets (torch.Tensor): binary NxK tensort that encodes which of the K
            classes are associated with the N-th input
            (eg: a row [0, 1, 0, 1] indicates that the example is
            associated with classes 2 and 4)
        threshold (float): threshold for for model output
        activation (str): activation to use for model output
        eps (float): epsilon to avoid zero division
    
    Extended version of 
        https://github.com/catalyst-team/catalyst/blob/master/catalyst/utils/metrics/accuracy.py#L58

    Returns:
        computed multi-label metrics
    """
    outputs, targets, _ = preprocess_multi_label_metrics(
        outputs=outputs, targets=targets
    )
    activation_fn = get_activation_fn(activation)
    outputs = activation_fn(outputs)

    outputs = (outputs > threshold).long()

    accuracy = (targets.long() == outputs.long()).sum().float() / np.prod(
        targets.shape
    )

    intersection = (outputs.long() * targets.long()).sum(axis=1).float()
    num_predicted = outputs.long().sum(axis=1).float()
    num_relevant = targets.long().sum(axis=1).float()
    union = num_predicted + num_relevant

    # Precision = ({predicted items} && {relevant items}) / {predicted items}
    precision = intersection / (num_predicted + eps * (num_predicted == 0))
    # Recall = ({predicted items} && {relevant items}) / {relevant items}
    recall = intersection / (num_relevant + eps * (num_relevant == 0))
    # IoU = ({predicted items} && {relevant items}) / ({predicted items} || {relevant items})
    iou = (intersection + eps * (union == 0)) / (union - intersection + eps)

    return accuracy, precision.mean(), recall.mean(), iou.mean()


def precision_at_k(
    actual: torch.Tensor, 
    predicted: torch.Tensor, 
    k: int,
):
    """
    Computes precision at cutoff k for one sample

    Args:
       actual: (torch.Tensor): tensor of length K with predicted item_ids sorted by relevance
       predicted (torch.Tensor): binary tensor that encodes which of the K
           classes are associated with the N-th input
           (eg: a row [0, 1, 0, 1] indicates that the example is
           associated with classes 2 and 4)
       k (int): parameter k of precison@k

    Returns:
       Computed value of precision@k for given sample
    """
    p_at_k = 0.0
    for item in predicted[:k]:
        if actual[item]:
            p_at_k += 1
    p_at_k /= k

    return p_at_k


def average_precision_at_k(
    actual: torch.Tensor, 
    predicted: torch.Tensor, 
    k: int,
) -> float:
    """
    Computes average precision at cutoff k for one sample

    Args:
      actual: (torch.Tensor): tensor of length K with predicted item_ids sorted by relevance
      predicted (torch.Tensor): binary tensor that encodes which of the K
          classes are associated with the N-th input
          (eg: a row [0, 1, 0, 1] indicates that the example is
          associated with classes 2 and 4)
      k (int): parameter k of AP@k

    Returns:
        Computed value of AP@k for given sample
    """
    ap_at_k = 0.0
    for idx, item in enumerate(predicted[:k]):
        if actual[item]:
            ap_at_k += precision_at_k(actual, predicted, k=idx + 1)
    ap_at_k /= min(k, actual.sum().cpu().numpy())
    

    return ap_at_k


def mean_average_precision_at_k(
    output: torch.Tensor, target: torch.Tensor, top_k: Tuple[int, ...] = (1,)
) -> List[float]:
    """
    Computes mean_average_precision_at_k at set of cutoff parameters K

    Args:
       outputs (torch.Tensor): NxK tensor that for each of the N examples
           indicates the probability of the example belonging to each of
           the K classes, according to the model.
       targets (torch.Tensor): binary NxK tensort that encodes which of the K
           classes are associated with the N-th input
           (eg: a row [0, 1, 0, 1] indicates that the example is
           associated with classes 2 and 4)
       top_k (tuple): list of parameters k at which map@k will be computed


    Returns:
       List of computed values of map@k at each cutoff k from topk
    """
    max_k = max(top_k)
    batch_size = target.size(0)

    _, top_indices = output.topk(k=max_k, dim=1, largest=True, sorted=True)

    result = []
    for k in top_k:  # loop over k
        map_at_k = 0.0
        for actual_target, predicted_items in zip(
            target, top_indices
        ):  # loop over samples
            map_at_k += average_precision_at_k(
                actual_target, predicted_items, k
            )
        map_at_k = map_at_k / batch_size
        result.append(map_at_k)

    return result

In [37]:
# What is Runner?
# https://catalyst-team.github.io/catalyst/api/core.html#runner
class CustomRunner(dl.Runner):

    def _handle_batch(self, batch):
        # model train/valid step
        features, targets = batch["features"], batch["targets"]
        logits = self.model(features)
        scores = torch.sigmoid(logits)

        loss = self.criterion(logits, targets)
        accuracy, precision, recall, iou = multi_label_metrics(
            logits, targets, threshold=0.5, activation="Sigmoid"
        )
        map05, map10, map20, map30 = mean_average_precision_at_k(
            scores, targets, top_k=(5, 10, 20, 30)
        )
        
        
        self.input = {"features": features, "targets": targets}
        self.output = {"logits": logits, "scores": scores}
        if not self.is_train_loader:
            batch_metrics = {
                                "loss": loss,
                                "precision": precision,
                                "recall": recall,
                                "map30": map30
                            }
            self.batch_metrics.update(batch_metrics)

        if self.is_train_loader:
            batch_metrics = {
                                "loss": loss,
                            }
            
            self.batch_metrics.update(batch_metrics)
            
            loss.backward()
            self.optimizer.step()
            self.optimizer.zero_grad()
    
    def predict_batch(self, batch):
        # model inference step
        batch = utils.maybe_recursive_call(batch, "to", device=self.device)
        logits = self.model(batch["features"])
        scores = torch.sigmoid(logits)
        return scores

In [38]:
model = Model()
criterion = nn.BCEWithLogitsLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=0.001)

loaders = {"train": train_loader, "valid": valid_loader}

In [ ]:
%load_ext tensorboard
%tensorboard --logdir ./logs

In [39]:
# For other minimal examples, please follow the link below
# https://github.com/catalyst-team/catalyst#minimal-examples
runner = CustomRunner()
# model training
runner.train(
    model=model,
    criterion=criterion,
    optimizer=optimizer,
    scheduler=None,
    loaders=loaders,
    logdir="./logs/baseline_map30",
    num_epochs=10,
    verbose=True,
    load_best_on_end=True,
    overfit=False,  #  <<<--- DO NOT FORGET TO MAKE IT ``False`` 
                    #  (``True`` uses only one batch to check pipeline correctness)
    callbacks=[
        # https://scikit-learn.org/stable/modules/generated/sklearn.metrics.average_precision_score.html
        # dl.AveragePrecisionCallback(input_key="targets", output_key="scores", prefix="ap"),
        # https://scikit-learn.org/stable/modules/generated/sklearn.metrics.roc_auc_score.html
        # dl.AUCCallback(input_key="targets", output_key="scores", prefix="auc"),
    ],
    main_metric="map30", # "ap/mean", 
    minimize_metric=False,
)


1/10 * Epoch (train):   0% 0/3803 [00:00<?, ?it/s]
1/10 * Epoch (train):   0% 0/3803 [00:00<?, ?it/s, loss=0.698]
1/10 * Epoch (train):   0% 1/3803 [00:00<36:43,  1.73it/s, loss=0.698]
1/10 * Epoch (train):   0% 1/3803 [00:00<36:43,  1.73it/s, loss=0.650]
1/10 * Epoch (train):   0% 2/3803 [00:00<31:04,  2.04it/s, loss=0.650]
1/10 * Epoch (train):   0% 2/3803 [00:01<31:04,  2.04it/s, loss=0.600]
1/10 * Epoch (train):   0% 3/3803 [00:01<26:37,  2.38it/s, loss=0.600]
1/10 * Epoch (train):   0% 3/3803 [00:01<26:37,  2.38it/s, loss=0.550]
1/10 * Epoch (train):   0% 4/3803 [00:01<22:59,  2.75it/s, loss=0.550]
1/10 * Epoch (train):   0% 4/3803 [00:01<22:59,  2.75it/s, loss=0.497]
1/10 * Epoch (train):   0% 5/3803 [00:01<21:11,  2.99it/s, loss=0.497]
1/10 * Epoch (train):   0% 5/3803 [00:01<21:11,  2.99it/s, loss=0.444]
1/10 * Epoch (train):   0% 6/3803 [00:01<19:54,  3.18it/s, loss=0.444]
1/10 * Epoch (train):   0% 6/3803 [00:02<19:54,  3.18it/s, loss=0.391]
1/10 * Epoch (train):   0% 7/3803

1/10 * Epoch (train):   1% 54/3803 [00:24<30:25,  2.05it/s, loss=0.057]
1/10 * Epoch (train):   1% 55/3803 [00:24<30:02,  2.08it/s, loss=0.057]
1/10 * Epoch (train):   1% 55/3803 [00:24<30:02,  2.08it/s, loss=0.062]
1/10 * Epoch (train):   1% 56/3803 [00:24<29:55,  2.09it/s, loss=0.062]
1/10 * Epoch (train):   1% 56/3803 [00:25<29:55,  2.09it/s, loss=0.067]
1/10 * Epoch (train):   1% 57/3803 [00:25<30:00,  2.08it/s, loss=0.067]
1/10 * Epoch (train):   1% 57/3803 [00:25<30:00,  2.08it/s, loss=0.058]
1/10 * Epoch (train):   2% 58/3803 [00:25<29:19,  2.13it/s, loss=0.058]
1/10 * Epoch (train):   2% 58/3803 [00:26<29:19,  2.13it/s, loss=0.055]
1/10 * Epoch (train):   2% 59/3803 [00:26<28:58,  2.15it/s, loss=0.055]
1/10 * Epoch (train):   2% 59/3803 [00:26<28:58,  2.15it/s, loss=0.080]
1/10 * Epoch (train):   2% 60/3803 [00:26<30:32,  2.04it/s, loss=0.080]
1/10 * Epoch (train):   2% 60/3803 [00:27<30:32,  2.04it/s, loss=0.061]
1/10 * Epoch (train):   2% 61/3803 [00:27<29:56,  2.08it/s, loss

1/10 * Epoch (train):   3% 109/3803 [00:50<29:59,  2.05it/s, loss=0.067]
1/10 * Epoch (train):   3% 109/3803 [00:51<29:59,  2.05it/s, loss=0.070]
1/10 * Epoch (train):   3% 110/3803 [00:51<31:00,  1.98it/s, loss=0.070]
1/10 * Epoch (train):   3% 110/3803 [00:51<31:00,  1.98it/s, loss=0.068]
1/10 * Epoch (train):   3% 111/3803 [00:51<31:30,  1.95it/s, loss=0.068]
1/10 * Epoch (train):   3% 111/3803 [00:52<31:30,  1.95it/s, loss=0.069]
1/10 * Epoch (train):   3% 112/3803 [00:52<31:31,  1.95it/s, loss=0.069]
1/10 * Epoch (train):   3% 112/3803 [00:52<31:31,  1.95it/s, loss=0.061]
1/10 * Epoch (train):   3% 113/3803 [00:52<30:35,  2.01it/s, loss=0.061]
1/10 * Epoch (train):   3% 113/3803 [00:53<30:35,  2.01it/s, loss=0.069]
1/10 * Epoch (train):   3% 114/3803 [00:53<31:05,  1.98it/s, loss=0.069]
1/10 * Epoch (train):   3% 114/3803 [00:53<31:05,  1.98it/s, loss=0.064]
1/10 * Epoch (train):   3% 115/3803 [00:53<30:07,  2.04it/s, loss=0.064]
1/10 * Epoch (train):   3% 115/3803 [00:54<30:07,  

1/10 * Epoch (train):   4% 162/3803 [01:18<31:43,  1.91it/s, loss=0.062]
1/10 * Epoch (train):   4% 163/3803 [01:18<31:47,  1.91it/s, loss=0.062]
1/10 * Epoch (train):   4% 163/3803 [01:19<31:47,  1.91it/s, loss=0.058]
1/10 * Epoch (train):   4% 164/3803 [01:19<31:05,  1.95it/s, loss=0.058]
1/10 * Epoch (train):   4% 164/3803 [01:19<31:05,  1.95it/s, loss=0.062]
1/10 * Epoch (train):   4% 165/3803 [01:19<31:13,  1.94it/s, loss=0.062]
1/10 * Epoch (train):   4% 165/3803 [01:20<31:13,  1.94it/s, loss=0.052]
1/10 * Epoch (train):   4% 166/3803 [01:20<29:27,  2.06it/s, loss=0.052]
1/10 * Epoch (train):   4% 166/3803 [01:20<29:27,  2.06it/s, loss=0.068]
1/10 * Epoch (train):   4% 167/3803 [01:20<30:11,  2.01it/s, loss=0.068]
1/10 * Epoch (train):   4% 167/3803 [01:21<30:11,  2.01it/s, loss=0.070]
1/10 * Epoch (train):   4% 168/3803 [01:21<31:14,  1.94it/s, loss=0.070]
1/10 * Epoch (train):   4% 168/3803 [01:21<31:14,  1.94it/s, loss=0.057]
1/10 * Epoch (train):   4% 169/3803 [01:21<30:56,  

1/10 * Epoch (train):   6% 216/3803 [01:45<29:49,  2.00it/s, loss=0.063]
1/10 * Epoch (train):   6% 216/3803 [01:46<29:49,  2.00it/s, loss=0.070]
1/10 * Epoch (train):   6% 217/3803 [01:46<31:05,  1.92it/s, loss=0.070]
1/10 * Epoch (train):   6% 217/3803 [01:46<31:05,  1.92it/s, loss=0.061]
1/10 * Epoch (train):   6% 218/3803 [01:46<31:02,  1.93it/s, loss=0.061]
1/10 * Epoch (train):   6% 218/3803 [01:47<31:02,  1.93it/s, loss=0.076]
1/10 * Epoch (train):   6% 219/3803 [01:47<31:38,  1.89it/s, loss=0.076]
1/10 * Epoch (train):   6% 219/3803 [01:47<31:38,  1.89it/s, loss=0.051]
1/10 * Epoch (train):   6% 220/3803 [01:47<30:06,  1.98it/s, loss=0.051]
1/10 * Epoch (train):   6% 220/3803 [01:48<30:06,  1.98it/s, loss=0.071]
1/10 * Epoch (train):   6% 221/3803 [01:48<31:04,  1.92it/s, loss=0.071]
1/10 * Epoch (train):   6% 221/3803 [01:48<31:04,  1.92it/s, loss=0.069]
1/10 * Epoch (train):   6% 222/3803 [01:48<31:36,  1.89it/s, loss=0.069]
1/10 * Epoch (train):   6% 222/3803 [01:49<31:36,  

...

10/10 * Epoch (valid):  49% 133/271 [01:06<01:04,  2.16it/s, loss=0.054, map30=0.639, precision=0.744, recall=0.544]
10/10 * Epoch (valid):  49% 134/271 [01:06<01:07,  2.02it/s, loss=0.054, map30=0.639, precision=0.744, recall=0.544]
10/10 * Epoch (valid):  49% 134/271 [01:06<01:07,  2.02it/s, loss=0.051, map30=0.623, precision=0.575, recall=0.573]
10/10 * Epoch (valid):  50% 135/271 [01:06<01:07,  2.03it/s, loss=0.051, map30=0.623, precision=0.575, recall=0.573]
10/10 * Epoch (valid):  50% 135/271 [01:07<01:07,  2.03it/s, loss=0.049, map30=0.669, precision=0.684, recall=0.581]
10/10 * Epoch (valid):  50% 136/271 [01:07<01:08,  1.98it/s, loss=0.049, map30=0.669, precision=0.684, recall=0.581]
10/10 * Epoch (valid):  50% 136/271 [01:07<01:08,  1.98it/s, loss=0.050, map30=0.674, precision=0.591, recall=0.664]
10/10 * Epoch (valid):  51% 137/271 [01:07<01:06,  2.02it/s, loss=0.050, map30=0.674, precision=0.591, recall=0.664]
10/10 * Epoch (valid):  51% 137/271 [01:08<01:06,  2.02it/s, los

10/10 * Epoch (valid):  62% 167/271 [01:23<00:51,  2.00it/s, loss=0.054, map30=0.637, precision=0.673, recall=0.577]
10/10 * Epoch (valid):  62% 168/271 [01:23<00:52,  1.97it/s, loss=0.054, map30=0.637, precision=0.673, recall=0.577]
10/10 * Epoch (valid):  62% 168/271 [01:23<00:52,  1.97it/s, loss=0.049, map30=0.636, precision=0.651, recall=0.634]
10/10 * Epoch (valid):  62% 169/271 [01:23<00:50,  2.03it/s, loss=0.049, map30=0.636, precision=0.651, recall=0.634]
10/10 * Epoch (valid):  62% 169/271 [01:24<00:50,  2.03it/s, loss=0.051, map30=0.654, precision=0.610, recall=0.532]
10/10 * Epoch (valid):  63% 170/271 [01:24<00:49,  2.06it/s, loss=0.051, map30=0.654, precision=0.610, recall=0.532]
10/10 * Epoch (valid):  63% 170/271 [01:24<00:49,  2.06it/s, loss=0.056, map30=0.622, precision=0.625, recall=0.552]
10/10 * Epoch (valid):  63% 171/271 [01:24<00:48,  2.07it/s, loss=0.056, map30=0.622, precision=0.625, recall=0.552]
10/10 * Epoch (valid):  63% 171/271 [01:25<00:48,  2.07it/s, los

10/10 * Epoch (valid):  74% 201/271 [01:40<00:35,  1.96it/s, loss=0.051, map30=0.648, precision=0.630, recall=0.573]
10/10 * Epoch (valid):  75% 202/271 [01:40<00:34,  1.99it/s, loss=0.051, map30=0.648, precision=0.630, recall=0.573]
10/10 * Epoch (valid):  75% 202/271 [01:40<00:34,  1.99it/s, loss=0.050, map30=0.646, precision=0.547, recall=0.562]
10/10 * Epoch (valid):  75% 203/271 [01:40<00:33,  2.01it/s, loss=0.050, map30=0.646, precision=0.547, recall=0.562]
10/10 * Epoch (valid):  75% 203/271 [01:41<00:33,  2.01it/s, loss=0.057, map30=0.632, precision=0.683, recall=0.536]
10/10 * Epoch (valid):  75% 204/271 [01:41<00:34,  1.94it/s, loss=0.057, map30=0.632, precision=0.683, recall=0.536]
10/10 * Epoch (valid):  75% 204/271 [01:41<00:34,  1.94it/s, loss=0.054, map30=0.615, precision=0.585, recall=0.576]
10/10 * Epoch (valid):  76% 205/271 [01:41<00:34,  1.92it/s, loss=0.054, map30=0.615, precision=0.585, recall=0.576]
10/10 * Epoch (valid):  76% 205/271 [01:42<00:34,  1.92it/s, los

10/10 * Epoch (valid):  87% 235/271 [01:57<00:17,  2.03it/s, loss=0.055, map30=0.640, precision=0.649, recall=0.566]
10/10 * Epoch (valid):  87% 236/271 [01:57<00:17,  2.02it/s, loss=0.055, map30=0.640, precision=0.649, recall=0.566]
10/10 * Epoch (valid):  87% 236/271 [01:57<00:17,  2.02it/s, loss=0.053, map30=0.651, precision=0.632, recall=0.637]
10/10 * Epoch (valid):  87% 237/271 [01:57<00:16,  2.01it/s, loss=0.053, map30=0.651, precision=0.632, recall=0.637]
10/10 * Epoch (valid):  87% 237/271 [01:58<00:16,  2.01it/s, loss=0.045, map30=0.692, precision=0.617, recall=0.622]
10/10 * Epoch (valid):  88% 238/271 [01:58<00:16,  2.04it/s, loss=0.045, map30=0.692, precision=0.617, recall=0.622]
10/10 * Epoch (valid):  88% 238/271 [01:58<00:16,  2.04it/s, loss=0.047, map30=0.711, precision=0.660, recall=0.639]
10/10 * Epoch (valid):  88% 239/271 [01:58<00:15,  2.02it/s, loss=0.047, map30=0.711, precision=0.660, recall=0.639]
10/10 * Epoch (valid):  88% 239/271 [01:59<00:15,  2.02it/s, los

10/10 * Epoch (valid):  99% 269/271 [02:14<00:01,  1.92it/s, loss=0.063, map30=0.607, precision=0.665, recall=0.544]
10/10 * Epoch (valid): 100% 270/271 [02:14<00:00,  1.87it/s, loss=0.063, map30=0.607, precision=0.665, recall=0.544]
10/10 * Epoch (valid): 100% 270/271 [02:14<00:00,  1.87it/s, loss=0.046, map30=0.693, precision=0.578, recall=0.644]
10/10 * Epoch (valid): 100% 271/271 [02:14<00:00,  2.10it/s, loss=0.046, map30=0.693, precision=0.578, recall=0.644]
10/10 * Epoch (valid): 100% 271/271 [02:14<00:00,  2.01it/s, loss=0.046, map30=0.693, precision=0.578, recall=0.644]
[2020-09-20 00:55:52,084] 
10/10 * Epoch 10 (train): loss=0.0505
10/10 * Epoch 10 (valid): loss=0.0506 | map30=0.6589 | precision=0.6364 | recall=0.5907
[2020-09-20 00:55:52,084] 
10/10 * Epoch 10 (train): loss=0.0505
10/10 * Epoch 10 (valid): loss=0.0506 | map30=0.6589 | precision=0.6364 | recall=0.5907
Top best models:
logs/baseline_map30/checkpoints/train.9.pth	0.6614
=> Loading checkpoint logs/baseline_map30

In [ ]:
# model inference example
# for prediction in runner.predict_loader(loader=loaders["valid"]):
#     assert prediction.detach().cpu().numpy().shape[-1] == MERCH_TYPE_NCLASSES-1

In [ ]:
# import plotly  # required for contrib
# from catalyst.contrib.utils import plot_tensorboard_log

# plot_tensorboard_log(logdir="./logs", step="batch")

In [ ]:
import plotly  # required for contrib
from catalyst.contrib.utils import plot_tensorboard_log

plot_tensorboard_log(
    logdir="./logs", 
    step="epoch", 
    metrics=[
        "loss", "accuracy", "precision", "recall", "iou", 
        "map05", "map10", "map20",
        "ap/mean", "auc/mean"
    ]
)

## Your task

We suggest you to improve this baseline. Feel free to use any kind of model architectures, loss functions, inputs, etc. in your experiments.


YOUR TASK is to predict purchases in `merchant_type` in **January-February 2020** for all the clients (50k) from the given dataset.

SUBMISSION FORMAT: You should submit a `.csv` file in the following format. 

The submission file should contain two columns:
* `party_rk` -- client unique identifier
* `recommendations` -- list of the **top 30** predicted `merchant_type`, sorted by predicted proba (pay attention!) **separated by commas**. 

The `.csv` file separator should be **semicolon (";")**. The submission file example can be generated by the pipeline shown below.

EVALUATION: Your submission will be evaluated by metric **MAP@30**. Scores for this part of the hackathon will be given according to the value of this metric.

Good luck!

## Submission file example

In [ ]:
# create data loader for submission
full_party = pd.read_csv(transactions_path, usecols=['party_rk']).party_rk.unique()
full_sum, full_trans_type, full_merchant_type, full_labels = prepare_data(
    full_party, mode="submission"
)
full_dataset = RSDataset(
   full_sum, full_trans_type, full_merchant_type, full_labels
)
full_loader = DataLoader(
    full_dataset, batch_size=64, shuffle=False, num_workers=8, drop_last=False)

In [ ]:
# get predictions from the model
predictions = []
for scores in tqdm(runner.predict_loader(loader=full_loader), total = len(full_loader)):
    _, top_indices = scores.topk(k=30, dim=1, largest=True, sorted=True)
    top_indices += 1
    predictions += top_indices.detach().cpu().tolist()

In [ ]:
# inverse mapping for merchant_type in predictions
merchant_type_inverse_mapping = {k: v for v, k in mappings['merchant_type'].items()}
def inverse_mapping(x):
    return list(map(merchant_type_inverse_mapping.get, x))

predictions = list(map(inverse_mapping, predictions))

In [ ]:
# create submission table
submission = pd.DataFrame({
    "party_rk" : full_party, 
    "recommendations" : predictions
})
submission['recommendations'] = submission['recommendations'].apply(lambda x: ",".join(map(str, x)))

submission.to_csv('submission_[TEAM_NAME].csv', index=False, sep=";")